In [1]:
import pandas as pd
import collections
import math
import os

import cv2
import matplotlib.pyplot as plt
import cv2
import sys
import numpy as np
import math
import time
from PIL import Image 

from pandas import read_csv  
import configparser

config = configparser.ConfigParser()
config.read('configtest.txt')

source_folder = config.get('Configuration', 'source_folder')
time_step = int(config.get('Configuration', 'time_step'))
data_folder = config.get('Configuration', 'data_folder')
ini_date = config.get('Configuration', 'ini_date')
end_date = config.get('Configuration', 'end_date')

window_size = int(config.get('Configuration', 'window_size'))

scenes=config.get('Configuration', 'scenes')
scenes = [(item.strip()) for item in scenes.split(',')]

print(scenes)

users=config.get('Configuration', 'users')
users = [(item.strip()) for item in users.split(',')]

anchors=config.get('Configuration', 'anchors')
anchors = [(item.strip()) for item in anchors.split(',')]

room=config.get('Configuration', 'room')

w = int(config.get(room, 'w'))
h = int(config.get(room, 'h'))

user_color={}
for user in users:
    user_color[user]=config.get('Colors', user)
print(user_color)


['Scene1', 'Scene2', 'Scene3', 'Scene4', 'Scene5', 'Scene6']
{'f02e': 'blue', '867f': 'red'}


In [2]:
import numpy as np
from pandas import read_csv    
import pandas as pd
import time

from datetime import datetime

off_zone=60*60*2

def day_time(ti):
    return int((int)((ti+off_zone)/(60*60*24)))


def time2str(tt):
    return datetime.fromtimestamp(tt).strftime("%Y-%m-%d %H:%M:%S")


t0 = (int)(datetime.strptime(ini_date, '%Y-%m-%d %H:%M:%S').timestamp())
print (ini_date,"Init date is", t0, "day:",day_time(t0), time2str(t0))

tN = (int)(datetime.strptime(end_date, '%Y-%m-%d %H:%M:%S').timestamp())
print (end_date,"End date is", tN, "day:",day_time(tN), time2str(tN))


def day_time0(ti):
    return day_time(ti)-day_time(t0)+1

def relT(ti):
    return (int)((ti-t0)/time_step)

days=list(range(day_time(t0),day_time(tN)+1))
print(days)

i0=0
ts=list(range(t0,tN,1))
print(i0,ts)
print(len(ts))

2024-03-16 19:30:50 Init date is 1710613850 day: 19798 2024-03-16 19:30:50
2024-03-16 20:26:35 End date is 1710617195 day: 19798 2024-03-16 20:26:35
[19798]
0 [1710613850, 1710613851, 1710613852, 1710613853, 1710613854, 1710613855, 1710613856, 1710613857, 1710613858, 1710613859, 1710613860, 1710613861, 1710613862, 1710613863, 1710613864, 1710613865, 1710613866, 1710613867, 1710613868, 1710613869, 1710613870, 1710613871, 1710613872, 1710613873, 1710613874, 1710613875, 1710613876, 1710613877, 1710613878, 1710613879, 1710613880, 1710613881, 1710613882, 1710613883, 1710613884, 1710613885, 1710613886, 1710613887, 1710613888, 1710613889, 1710613890, 1710613891, 1710613892, 1710613893, 1710613894, 1710613895, 1710613896, 1710613897, 1710613898, 1710613899, 1710613900, 1710613901, 1710613902, 1710613903, 1710613904, 1710613905, 1710613906, 1710613907, 1710613908, 1710613909, 1710613910, 1710613911, 1710613912, 1710613913, 1710613914, 1710613915, 1710613916, 1710613917, 1710613918, 1710613919, 

In [3]:
scene_user = {}
lista_timestamps=[]
for d in days:
    for user in users:
        scene_user[user] = {}
        for s in scenes:
            print(d,source_folder+"/"+s+"/location_gt_"+user+"/"+str(d)+".location.tsv")
            try:
                series=read_csv(source_folder+"/"+s+"/location_gt_"+user+"/"+str(d)+".location.tsv", sep="\t",parse_dates=True, header=None, names=["time","date","time2","x","y"])
                print(d,series.size,(series["time"].iloc[0],series["time"].iloc[-1]))
                scene_user[user][s] = (series["time"].iloc[0],series["time"].iloc[-1])
                #print("test")
                print(scene_user[user][s])
                #if user=='ed9c':
                lista_timestamps.extend(list(range(scene_user[user][s][0],scene_user[user][s][1],1)))
                #print(lista_timestamps)
                #print("test2")
            except Exception as e:
                print("Not data",e)
                continue
def getScene(t0):
    for user, user_scene in scene_user.items():
        for scene, times in user_scene.items():
            #print(t0,times[0],times[1])
            if(t0>times[0]-window_size/2 and t0<times[1]+window_size/2):
                return scene
    return None

19798 ./data/livingroom/2-person-labelled//Scene1/location_gt_f02e/19798.location.tsv
19798 1960 (1710613851, 1710614183)
(1710613851, 1710614183)
19798 ./data/livingroom/2-person-labelled//Scene2/location_gt_f02e/19798.location.tsv
19798 2510 (1710614425, 1710614773)
(1710614425, 1710614773)
19798 ./data/livingroom/2-person-labelled//Scene3/location_gt_f02e/19798.location.tsv
19798 2290 (1710615299, 1710615618)
(1710615299, 1710615618)
19798 ./data/livingroom/2-person-labelled//Scene4/location_gt_f02e/19798.location.tsv
19798 2085 (1710615774, 1710616088)
(1710615774, 1710616088)
19798 ./data/livingroom/2-person-labelled//Scene5/location_gt_f02e/19798.location.tsv
19798 1660 (1710616615, 1710616905)
(1710616615, 1710616905)
19798 ./data/livingroom/2-person-labelled//Scene6/location_gt_f02e/19798.location.tsv
19798 1290 (1710617082, 1710617196)
(1710617082, 1710617196)
19798 ./data/livingroom/2-person-labelled//Scene1/location_gt_867f/19798.location.tsv
19798 1350 (1710613852, 17106141

In [4]:
#print(len(lista_timestamps))
def getFPImg(tt):
    return np.array(Image.open(data_folder+"/"+room+"/DAY_"+str(day)+"/FP."+str(tt)+".png"))/255.0

def getGTImg(tt,user):
    #try:
    return np.array(Image.open(data_folder+"/"+room+"/DAY_"+str(day)+"/GT."+user+"."+str(tt)+".png"))/255.0
    #except FileNotFoundError:
     #   print("File not found")
     #   return None

In [5]:
#ts=lista_timestamps
#print(ts)
XY0={}
rssi0={}
Y0={}

T0_user={}
T0=[]
T1=[]
for day in days:
    anchors_data={}
    for user in users:
        XY0[user]=[]
        rssi0[user]=[]
        Y0[user]=[]
        T0_user[user]=[]


        anchors_data[user]={}
        for anchor in anchors:
            print(data_folder+"/"+room+"/DAY_"+str(day)+"/"+user+"."+anchor+".tsv")
            print(user,anchor)
            series=read_csv(data_folder+"/"+room+"/DAY_"+str(day)+"/"+user+"."+anchor+".tsv", sep="\t",parse_dates=True, header=None, names=["time","d"])
            series=series.values
            anchors_data[user][anchor]=series
            

    for it,tt in enumerate(ts):
        print(it,tt)
        imgX=getFPImg(tt)
        print("imgX",imgX.shape)

        for user in users:
            
            imgY=getGTImg(tt,user)
            #if imgY is None:
            #    continue
            print("user",user,"imgY",imgY.shape)

            dist=[]
            for ixa,anchor in enumerate(anchors):
                d=anchors_data[user][anchor][it][1]
                if(d>0):
                    d=d/10.0
                if(d>1):
                    d=1
                print("\t anchor:",anchor, anchors_data[user][anchor][it], "tt:",tt)
                dist.append(d)

            dist=np.array(dist)
            print("dist:",dist)

            rssi0[user].append(dist.reshape(len(anchors),1))
            XY0[user].append(imgX[:, :, np.newaxis])
            Y0[user].append(imgY[:, :, np.newaxis])
            T0_user[user].append(it)
            T0.append(it)
            T1.append(tt)
print(T0)        
print(T1)        
print(len(T1))
T0=list(dict.fromkeys(T0))
T1=list(dict.fromkeys(T1))
print(T0)        
print(T1)
#print(T0_user)

./2p-livingroom/livingroom/DAY_19798/f02e.8171.tsv
f02e 8171
./2p-livingroom/livingroom/DAY_19798/f02e.eb38.tsv
f02e eb38
./2p-livingroom/livingroom/DAY_19798/867f.8171.tsv
867f 8171
./2p-livingroom/livingroom/DAY_19798/867f.eb38.tsv
867f eb38
0 1710613850
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061385e+09 5.14200000e+00] tt: 1710613850
	 anchor: eb38 [1.71061385e+09 3.58200000e+00] tt: 1710613850
dist: [0.5142 0.3582]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061385e+09 4.91200000e+00] tt: 1710613850
	 anchor: eb38 [1.71061385e+09 3.56800000e+00] tt: 1710613850
dist: [0.4912 0.3568]
1 1710613851
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061385e+09 5.14700000e+00] tt: 1710613851
	 anchor: eb38 [1.71061385e+09 3.69900000e+00] tt: 1710613851
dist: [0.5147 0.3699]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061385e+09 4.91200000e+00] tt: 1710613851
	 anchor: eb38 [1.71061385e+09 3.56800000e+00] tt: 1710613851
dist: [0.4912 0.3568]
2 1710613852
imgX (8, 8)
user f02e

imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061394e+09 -1.00000000e+00] tt: 1710613938
	 anchor: eb38 [ 1.71061394e+09 -1.00000000e+00] tt: 1710613938
dist: [-1. -1.]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061394e+09 -1.00000000e+00] tt: 1710613938
	 anchor: eb38 [ 1.71061394e+09 -1.00000000e+00] tt: 1710613938
dist: [-1. -1.]
89 1710613939
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061394e+09 7.68600000e+00] tt: 1710613939
	 anchor: eb38 [1.71061394e+09 6.80000000e-01] tt: 1710613939
dist: [0.7686 0.068 ]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061394e+09 -1.00000000e+00] tt: 1710613939
	 anchor: eb38 [ 1.71061394e+09 -1.00000000e+00] tt: 1710613939
dist: [-1. -1.]
90 1710613940
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061394e+09 7.68600000e+00] tt: 1710613940
	 anchor: eb38 [1.71061394e+09 6.80000000e-01] tt: 1710613940
dist: [0.7686 0.068 ]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061394e+09 -1.00000000e+00] tt: 1710613940
	 anchor: eb38 [

imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061399e+09 3.35300000e+00] tt: 1710613991
	 anchor: eb38 [1.71061399e+09 4.76300000e+00] tt: 1710613991
dist: [0.3353 0.4763]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061399e+09 5.97100000e+00] tt: 1710613991
	 anchor: eb38 [1.71061399e+09 1.76100000e+00] tt: 1710613991
dist: [0.5971 0.1761]
142 1710613992
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061399e+09 3.35300000e+00] tt: 1710613992
	 anchor: eb38 [1.71061399e+09 4.76300000e+00] tt: 1710613992
dist: [0.3353 0.4763]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061399e+09 5.97100000e+00] tt: 1710613992
	 anchor: eb38 [1.71061399e+09 1.76500000e+00] tt: 1710613992
dist: [0.5971 0.1765]
143 1710613993
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061399e+09 -1.00000000e+00] tt: 1710613993
	 anchor: eb38 [ 1.71061399e+09 -1.00000000e+00] tt: 1710613993
dist: [-1. -1.]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061399e+09 6.47200000e+00] tt: 1710613993
	 anchor: eb

user f02e imgY (8, 8)
	 anchor: 8171 [1.71061411e+09 5.35300000e+00] tt: 1710614112
	 anchor: eb38 [1.71061411e+09 2.74900000e+00] tt: 1710614112
dist: [0.5353 0.2749]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061411e+09 4.75800000e+00] tt: 1710614112
	 anchor: eb38 [ 1.71061411e+09 -1.00000000e+00] tt: 1710614112
dist: [ 0.4758 -1.    ]
263 1710614113
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061411e+09 5.72800000e+00] tt: 1710614113
	 anchor: eb38 [1.71061411e+09 2.49600000e+00] tt: 1710614113
dist: [0.5728 0.2496]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061411e+09 4.75800000e+00] tt: 1710614113
	 anchor: eb38 [ 1.71061411e+09 -1.00000000e+00] tt: 1710614113
dist: [ 0.4758 -1.    ]
264 1710614114
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061411e+09 5.73700000e+00] tt: 1710614114
	 anchor: eb38 [1.71061411e+09 2.21000000e+00] tt: 1710614114
dist: [0.5737 0.221 ]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061411e+09 -1.00000000e+00] tt: 1710614114
	 anchor: eb

user 867f imgY (8, 8)
	 anchor: 8171 [1.7106142e+09 5.5220000e+00] tt: 1710614199
	 anchor: eb38 [1.7106142e+09 2.3230000e+00] tt: 1710614199
dist: [0.5522 0.2323]
350 1710614200
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.7106142e+09 5.3490000e+00] tt: 1710614200
	 anchor: eb38 [1.7106142e+09 2.8420000e+00] tt: 1710614200
dist: [0.5349 0.2842]
user 867f imgY (8, 8)
	 anchor: 8171 [1.7106142e+09 5.5030000e+00] tt: 1710614200
	 anchor: eb38 [1.7106142e+09 2.3230000e+00] tt: 1710614200
dist: [0.5503 0.2323]
351 1710614201
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.7106142e+09 -1.0000000e+00] tt: 1710614201
	 anchor: eb38 [ 1.7106142e+09 -1.0000000e+00] tt: 1710614201
dist: [-1. -1.]
user 867f imgY (8, 8)
	 anchor: 8171 [1.7106142e+09 5.5030000e+00] tt: 1710614201
	 anchor: eb38 [1.7106142e+09 2.3040000e+00] tt: 1710614201
dist: [0.5503 0.2304]
352 1710614202
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.7106142e+09 -1.0000000e+00] tt: 1710614202
	 anchor: eb38 [ 

...

imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616752
	 anchor: eb38 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616752
dist: [-1. -1.]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616752
	 anchor: eb38 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616752
dist: [-1. -1.]
2903 1710616753
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616753
	 anchor: eb38 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616753
dist: [-1. -1.]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616753
	 anchor: eb38 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616753
dist: [-1. -1.]
2904 1710616754
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616754
	 anchor: eb38 [ 1.71061675e+09 -1.00000000e+00] tt: 1710616754
dist: [-1. -1.]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061675e+09 3.61500000e+00] tt: 1710616754
	 anchor: eb38 [1.

imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061685e+09 6.53300000e+00] tt: 1710616854
	 anchor: eb38 [1.71061685e+09 2.88500000e+00] tt: 1710616854
dist: [0.6533 0.2885]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061685e+09 4.75400000e+00] tt: 1710616854
	 anchor: eb38 [1.71061685e+09 3.63800000e+00] tt: 1710616854
dist: [0.4754 0.3638]
3005 1710616855
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061686e+09 6.64100000e+00] tt: 1710616855
	 anchor: eb38 [1.71061686e+09 2.37500000e+00] tt: 1710616855
dist: [0.6641 0.2375]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061686e+09 4.75400000e+00] tt: 1710616855
	 anchor: eb38 [1.71061686e+09 3.63800000e+00] tt: 1710616855
dist: [0.4754 0.3638]
3006 1710616856
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061686e+09 6.98400000e+00] tt: 1710616856
	 anchor: eb38 [1.71061686e+09 2.29500000e+00] tt: 1710616856
dist: [0.6984 0.2295]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061686e+09 4.73500000e+00] tt: 1710616856
	 anchor

user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616975
	 anchor: eb38 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616975
dist: [-1. -1.]
3126 1710616976
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616976
	 anchor: eb38 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616976
dist: [-1. -1.]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616976
	 anchor: eb38 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616976
dist: [-1. -1.]
3127 1710616977
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616977
	 anchor: eb38 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616977
dist: [-1. -1.]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616977
	 anchor: eb38 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616977
dist: [-1. -1.]
3128 1710616978
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061698e+09 -1.00000000e+00] tt: 1710616978


user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061705e+09 -1.00000000e+00] tt: 1710617051
	 anchor: eb38 [ 1.71061705e+09 -1.00000000e+00] tt: 1710617051
dist: [-1. -1.]
3202 1710617052
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061705e+09 5.99500000e+00] tt: 1710617052
	 anchor: eb38 [1.71061705e+09 2.28500000e+00] tt: 1710617052
dist: [0.5995 0.2285]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061705e+09 5.08100000e+00] tt: 1710617052
	 anchor: eb38 [1.71061705e+09 3.92400000e+00] tt: 1710617052
dist: [0.5081 0.3924]
3203 1710617053
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061705e+09 5.98100000e+00] tt: 1710617053
	 anchor: eb38 [1.71061705e+09 2.27100000e+00] tt: 1710617053
dist: [0.5981 0.2271]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061705e+09 5.02500000e+00] tt: 1710617053
	 anchor: eb38 [1.71061705e+09 3.70800000e+00] tt: 1710617053
dist: [0.5025 0.3708]
3204 1710617054
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061705e+09 5.98100000e+00] tt: 17106

user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061718e+09 -1.00000000e+00] tt: 1710617179
	 anchor: eb38 [ 1.71061718e+09 -1.00000000e+00] tt: 1710617179
dist: [-1. -1.]
3330 1710617180
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061718e+09 4.72100000e+00] tt: 1710617180
	 anchor: eb38 [1.71061718e+09 3.80700000e+00] tt: 1710617180
dist: [0.4721 0.3807]
user 867f imgY (8, 8)
	 anchor: 8171 [ 1.71061718e+09 -1.00000000e+00] tt: 1710617180
	 anchor: eb38 [ 1.71061718e+09 -1.00000000e+00] tt: 1710617180
dist: [-1. -1.]
3331 1710617181
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [1.71061718e+09 4.72100000e+00] tt: 1710617181
	 anchor: eb38 [1.71061718e+09 3.80700000e+00] tt: 1710617181
dist: [0.4721 0.3807]
user 867f imgY (8, 8)
	 anchor: 8171 [1.71061718e+09 5.20300000e+00] tt: 1710617181
	 anchor: eb38 [1.71061718e+09 2.73500000e+00] tt: 1710617181
dist: [0.5203 0.2735]
3332 1710617182
imgX (8, 8)
user f02e imgY (8, 8)
	 anchor: 8171 [ 1.71061718e+09 -1.00000000e+00] tt: 17106

In [6]:
for user in users:
    XY0[user]=np.array(XY0[user])
    rssi0[user]=np.array(rssi0[user])
    Y0[user]=np.array(Y0[user])
T0=np.array(T0)
print(T0)
print(len(T0))
#print(XY0.shape)
#frame0=np.median(XY0, axis=(0)).astype(np.uint8)
#for i in range(0,XY0.shape[0]):
#    XY0[i]=XY0[i]-frame0
#print(XY0.shape)

[   0    1    2 ... 3342 3343 3344]
3345


In [7]:
minT=np.min(T0)
maxT=np.max(T0)

print(T0)
print(len(T0))
print(minT)
print(maxT)

print(T1)
print(len(T1))

[   0    1    2 ... 3342 3343 3344]
3345
0
3344
[1710613850, 1710613851, 1710613852, 1710613853, 1710613854, 1710613855, 1710613856, 1710613857, 1710613858, 1710613859, 1710613860, 1710613861, 1710613862, 1710613863, 1710613864, 1710613865, 1710613866, 1710613867, 1710613868, 1710613869, 1710613870, 1710613871, 1710613872, 1710613873, 1710613874, 1710613875, 1710613876, 1710613877, 1710613878, 1710613879, 1710613880, 1710613881, 1710613882, 1710613883, 1710613884, 1710613885, 1710613886, 1710613887, 1710613888, 1710613889, 1710613890, 1710613891, 1710613892, 1710613893, 1710613894, 1710613895, 1710613896, 1710613897, 1710613898, 1710613899, 1710613900, 1710613901, 1710613902, 1710613903, 1710613904, 1710613905, 1710613906, 1710613907, 1710613908, 1710613909, 1710613910, 1710613911, 1710613912, 1710613913, 1710613914, 1710613915, 1710613916, 1710613917, 1710613918, 1710613919, 1710613920, 1710613921, 1710613922, 1710613923, 1710613924, 1710613925, 1710613926, 1710613927, 1710613928, 171

In [8]:
XYT=[]
rssiT=[]
YT=[]

TA=int(window_size/2)
TB=int(window_size/2)

T=window_size

S=[]
for user in users:
    print("Usuario ",user)
    for t in range(minT+TA,maxT-TB):

        
        tt=T1[t]
        scene=getScene(tt)
        
        print("Scene",scene,tt,t)
        if not scene:
            continue

        subW=list(range(t-TA,t+TB))
        print("subW:",subW, "t:",t)
        if not (set(subW).intersection(set(T0)) == set(subW)):
            print("Not data for sliding window!",t)
            continue

        #print("rssi0[t-T:t+T]",rssi0[t-T:t+T].flatten())
        if(all(map(lambda x: x == -1, rssi0[user][t-TA:t].flatten()))):
            print("Distance -1 for RSSI in sliding window!",t)
            continue

        if(all(map(lambda x: x == -1, rssi0[user][t:t+TB].flatten()))):
            print("Distance -1 for RSSI in sliding window!",t)
            continue

        if(all(map(lambda x: x == 0, Y0[user][t].flatten()))):
            print("Distance 0 for Y0 in t!",t)
            continue


        if(XY0[user][t-TA:t+TB].shape[0]!=T):
            print("#",XY0[user][t-TA:t+TB].shape)
            continue
        if(rssi0[user][t-TA:t+TB].shape[0]!=T):
            print("@",rssi0[user][t-TA:t+TB].shape)
            continue

        XYT.append(XY0[user][t-TA:t+TB])
        rssiT.append(rssi0[user][t-TA:t+TB])
        YT.append(Y0[user][t])
        S.append(scene)
        #print(S)
#print(S)
XYT=np.array(XYT)
rssiT=np.array(rssiT)
YT=np.array(YT)    
S=np.array(S)    
print(XYT.shape)
print(rssiT.shape)
print(YT.shape)


Usuario  f02e
Scene Scene1 1710613852 2
subW: [0, 1, 2, 3] t: 2
Scene Scene1 1710613853 3
subW: [1, 2, 3, 4] t: 3
Scene Scene1 1710613854 4
subW: [2, 3, 4, 5] t: 4
Distance -1 for RSSI in sliding window! 4
Scene Scene1 1710613855 5
subW: [3, 4, 5, 6] t: 5
Distance -1 for RSSI in sliding window! 5
Scene Scene1 1710613856 6
subW: [4, 5, 6, 7] t: 6
Distance -1 for RSSI in sliding window! 6
Scene Scene1 1710613857 7
subW: [5, 6, 7, 8] t: 7
Distance -1 for RSSI in sliding window! 7
Scene Scene1 1710613858 8
subW: [6, 7, 8, 9] t: 8
Distance -1 for RSSI in sliding window! 8
Scene Scene1 1710613859 9
subW: [7, 8, 9, 10] t: 9
Distance -1 for RSSI in sliding window! 9
Scene Scene1 1710613860 10
subW: [8, 9, 10, 11] t: 10
Scene Scene1 1710613861 11
subW: [9, 10, 11, 12] t: 11
Distance -1 for RSSI in sliding window! 11
Scene Scene1 1710613862 12
subW: [10, 11, 12, 13] t: 12
Distance -1 for RSSI in sliding window! 12
Scene Scene1 1710613863 13
subW: [11, 12, 13, 14] t: 13
Distance -1 for RSSI in sl

Scene Scene3 1710615580 1730
subW: [1728, 1729, 1730, 1731] t: 1730
Scene Scene3 1710615581 1731
subW: [1729, 1730, 1731, 1732] t: 1731
Scene Scene3 1710615582 1732
subW: [1730, 1731, 1732, 1733] t: 1732
Scene Scene3 1710615583 1733
subW: [1731, 1732, 1733, 1734] t: 1733
Scene Scene3 1710615584 1734
subW: [1732, 1733, 1734, 1735] t: 1734
Scene Scene3 1710615585 1735
subW: [1733, 1734, 1735, 1736] t: 1735
Scene Scene3 1710615586 1736
subW: [1734, 1735, 1736, 1737] t: 1736
Scene Scene3 1710615587 1737
subW: [1735, 1736, 1737, 1738] t: 1737
Scene Scene3 1710615588 1738
subW: [1736, 1737, 1738, 1739] t: 1738
Scene Scene3 1710615589 1739
subW: [1737, 1738, 1739, 1740] t: 1739
Distance -1 for RSSI in sliding window! 1739
Scene Scene3 1710615590 1740
subW: [1738, 1739, 1740, 1741] t: 1740
Distance -1 for RSSI in sliding window! 1740
Scene Scene3 1710615591 1741
subW: [1739, 1740, 1741, 1742] t: 1741
Distance -1 for RSSI in sliding window! 1741
Scene Scene3 1710615592 1742
subW: [1740, 1741, 1

Scene None 1710616531 2681
Scene None 1710616532 2682
Scene None 1710616533 2683
Scene None 1710616534 2684
Scene None 1710616535 2685
Scene None 1710616536 2686
Scene None 1710616537 2687
Scene None 1710616538 2688
Scene None 1710616539 2689
Scene None 1710616540 2690
Scene None 1710616541 2691
Scene None 1710616542 2692
Scene None 1710616543 2693
Scene None 1710616544 2694
Scene None 1710616545 2695
Scene None 1710616546 2696
Scene None 1710616547 2697
Scene None 1710616548 2698
Scene None 1710616549 2699
Scene None 1710616550 2700
Scene None 1710616551 2701
Scene None 1710616552 2702
Scene None 1710616553 2703
Scene None 1710616554 2704
Scene None 1710616555 2705
Scene None 1710616556 2706
Scene None 1710616557 2707
Scene None 1710616558 2708
Scene None 1710616559 2709
Scene None 1710616560 2710
Scene None 1710616561 2711
Scene None 1710616562 2712
Scene None 1710616563 2713
Scene None 1710616564 2714
Scene None 1710616565 2715
Scene None 1710616566 2716
Scene None 1710616567 2717
S

Scene Scene1 1710614130 280
subW: [278, 279, 280, 281] t: 280
Scene Scene1 1710614131 281
subW: [279, 280, 281, 282] t: 281
Distance -1 for RSSI in sliding window! 281
Scene Scene1 1710614132 282
subW: [280, 281, 282, 283] t: 282
Scene Scene1 1710614133 283
subW: [281, 282, 283, 284] t: 283
Distance -1 for RSSI in sliding window! 283
Scene Scene1 1710614134 284
subW: [282, 283, 284, 285] t: 284
Scene Scene1 1710614135 285
subW: [283, 284, 285, 286] t: 285
Scene Scene1 1710614136 286
subW: [284, 285, 286, 287] t: 286
Scene Scene1 1710614137 287
subW: [285, 286, 287, 288] t: 287
Scene Scene1 1710614138 288
subW: [286, 287, 288, 289] t: 288
Scene Scene1 1710614139 289
subW: [287, 288, 289, 290] t: 289
Scene Scene1 1710614140 290
subW: [288, 289, 290, 291] t: 290
Scene Scene1 1710614141 291
subW: [289, 290, 291, 292] t: 291
Scene Scene1 1710614142 292
subW: [290, 291, 292, 293] t: 292
Scene Scene1 1710614143 293
subW: [291, 292, 293, 294] t: 293
Scene Scene1 1710614144 294
subW: [292, 293,

Scene Scene2 1710614624 774
subW: [772, 773, 774, 775] t: 774
Distance -1 for RSSI in sliding window! 774
Scene Scene2 1710614625 775
subW: [773, 774, 775, 776] t: 775
Scene Scene2 1710614626 776
subW: [774, 775, 776, 777] t: 776
Scene Scene2 1710614627 777
subW: [775, 776, 777, 778] t: 777
Scene Scene2 1710614628 778
subW: [776, 777, 778, 779] t: 778
Scene Scene2 1710614629 779
subW: [777, 778, 779, 780] t: 779
Scene Scene2 1710614630 780
subW: [778, 779, 780, 781] t: 780
Scene Scene2 1710614631 781
subW: [779, 780, 781, 782] t: 781
Scene Scene2 1710614632 782
subW: [780, 781, 782, 783] t: 782
Scene Scene2 1710614633 783
subW: [781, 782, 783, 784] t: 783
Distance -1 for RSSI in sliding window! 783
Scene Scene2 1710614634 784
subW: [782, 783, 784, 785] t: 784
Distance -1 for RSSI in sliding window! 784
Scene Scene2 1710614635 785
subW: [783, 784, 785, 786] t: 785
Distance -1 for RSSI in sliding window! 785
Scene Scene2 1710614636 786
subW: [784, 785, 786, 787] t: 786
Distance -1 for RS

Scene Scene3 1710615504 1654
subW: [1652, 1653, 1654, 1655] t: 1654
Distance -1 for RSSI in sliding window! 1654
Scene Scene3 1710615505 1655
subW: [1653, 1654, 1655, 1656] t: 1655
Distance -1 for RSSI in sliding window! 1655
Scene Scene3 1710615506 1656
subW: [1654, 1655, 1656, 1657] t: 1656
Distance -1 for RSSI in sliding window! 1656
Scene Scene3 1710615507 1657
subW: [1655, 1656, 1657, 1658] t: 1657
Distance -1 for RSSI in sliding window! 1657
Scene Scene3 1710615508 1658
subW: [1656, 1657, 1658, 1659] t: 1658
Distance -1 for RSSI in sliding window! 1658
Scene Scene3 1710615509 1659
subW: [1657, 1658, 1659, 1660] t: 1659
Scene Scene3 1710615510 1660
subW: [1658, 1659, 1660, 1661] t: 1660
Scene Scene3 1710615511 1661
subW: [1659, 1660, 1661, 1662] t: 1661
Scene Scene3 1710615512 1662
subW: [1660, 1661, 1662, 1663] t: 1662
Scene Scene3 1710615513 1663
subW: [1661, 1662, 1663, 1664] t: 1663
Scene Scene3 1710615514 1664
subW: [1662, 1663, 1664, 1665] t: 1664
Scene Scene3 1710615515 166

Scene Scene5 1710616609 2759
subW: [2757, 2758, 2759, 2760] t: 2759
Scene Scene5 1710616610 2760
subW: [2758, 2759, 2760, 2761] t: 2760
Scene Scene5 1710616611 2761
subW: [2759, 2760, 2761, 2762] t: 2761
Scene Scene5 1710616612 2762
subW: [2760, 2761, 2762, 2763] t: 2762
Scene Scene5 1710616613 2763
subW: [2761, 2762, 2763, 2764] t: 2763
Scene Scene5 1710616614 2764
subW: [2762, 2763, 2764, 2765] t: 2764
Scene Scene5 1710616615 2765
subW: [2763, 2764, 2765, 2766] t: 2765
Scene Scene5 1710616616 2766
subW: [2764, 2765, 2766, 2767] t: 2766
Scene Scene5 1710616617 2767
subW: [2765, 2766, 2767, 2768] t: 2767
Scene Scene5 1710616618 2768
subW: [2766, 2767, 2768, 2769] t: 2768
Distance -1 for RSSI in sliding window! 2768
Scene Scene5 1710616619 2769
subW: [2767, 2768, 2769, 2770] t: 2769
Distance -1 for RSSI in sliding window! 2769
Scene Scene5 1710616620 2770
subW: [2768, 2769, 2770, 2771] t: 2770
Distance -1 for RSSI in sliding window! 2770
Scene Scene5 1710616621 2771
subW: [2769, 2770, 2

Scene Scene5 1710616878 3028
subW: [3026, 3027, 3028, 3029] t: 3028
Scene Scene5 1710616879 3029
subW: [3027, 3028, 3029, 3030] t: 3029
Scene Scene5 1710616880 3030
subW: [3028, 3029, 3030, 3031] t: 3030
Scene Scene5 1710616881 3031
subW: [3029, 3030, 3031, 3032] t: 3031
Scene Scene5 1710616882 3032
subW: [3030, 3031, 3032, 3033] t: 3032
Scene Scene5 1710616883 3033
subW: [3031, 3032, 3033, 3034] t: 3033
Scene Scene5 1710616884 3034
subW: [3032, 3033, 3034, 3035] t: 3034
Scene Scene5 1710616885 3035
subW: [3033, 3034, 3035, 3036] t: 3035
Scene Scene5 1710616886 3036
subW: [3034, 3035, 3036, 3037] t: 3036
Scene Scene5 1710616887 3037
subW: [3035, 3036, 3037, 3038] t: 3037
Distance -1 for RSSI in sliding window! 3037
Scene Scene5 1710616888 3038
subW: [3036, 3037, 3038, 3039] t: 3038
Distance -1 for RSSI in sliding window! 3038
Scene Scene5 1710616889 3039
subW: [3037, 3038, 3039, 3040] t: 3039
Distance -1 for RSSI in sliding window! 3039
Scene Scene5 1710616890 3040
subW: [3038, 3039, 3

In [9]:
import matplotlib.pyplot as plt

L=20

# Create a figure with two subplots (one row, two columns)
fig, axes = plt.subplots(L, 2, figsize=(200, 200))


for k in range(0,L):
    mpAll=XY0[users[0]][k].reshape(w,h)

    axes[k,0].imshow(mpAll, cmap='viridis', interpolation='nearest')
    axes[k,0].set_title('All players (last frame)')
    axes[k,0].axis('off')

    mpOne=Y0[users[0]][k].reshape(w,h)

    axes[k,1].imshow(mpOne, cmap='viridis', interpolation='nearest')
    axes[k,1].set_title('True (last frame) of player')
    axes[k,1].axis('off')

    
# Adjust spacing between subplots
plt.tight_layout()

# Show the plots
plt.show()

In [10]:
from tensorflow import keras

from tensorflow.keras import layers
from keras.optimizers import Adam
from keras.layers import MaxPooling2D,Activation, Dense

from tensorflow import Tensor
from tensorflow.keras.layers import Softmax,Input, Conv1D, Conv2D, ReLU, BatchNormalization,\
                                    Add, AveragePooling2D, Flatten, Dense,Dropout,LSTM,TimeDistributed,MaxPooling1D
from tensorflow.keras.models import Model

from sklearn.metrics import ConfusionMatrixDisplay
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report 
from keras.losses import mean_squared_error

from keras import backend as K

from sklearn.model_selection import KFold

from tensorflow import keras

from tensorflow.keras import layers
from keras.optimizers import Adam
from keras.layers import MaxPooling2D,Activation, Dense

from tensorflow import Tensor
from tensorflow.keras.layers import Lambda, Dot,Reshape,Multiply, Input, Conv1D, Conv2D, ConvLSTM2D,ReLU,UpSampling2D, BatchNormalization,\
                                    Add, AveragePooling2D, Flatten, Dense,Dropout,LSTM,TimeDistributed,MaxPooling1D, Concatenate
from tensorflow.keras.models import Model, Sequential

from keras import backend as K
import math

from tensorflow.keras.losses import CategoricalCrossentropy

import tensorflow as tf
from keras.models import load_model
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error, mean_absolute_error
from tensorflow.keras.layers import Conv2DTranspose

2025-02-25 14:21:28.099592: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-02-25 14:21:28.144352: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-02-25 14:21:28.662999: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [11]:
#MODELO A

K=len(anchors)
print(K)
print(T)
rssi = Input(shape=(T,K,1))
print(rssi)

encoded_rssi = TimeDistributed(Conv1D(32, 3, activation='relu', padding='same',
        input_shape=(T, K, 1)))(rssi)
#encoded_rssi = TimeDistributed(MaxPooling1D(2, padding='same'))(encoded_rssi)
encoded_rssi = TimeDistributed(Conv1D(64, 3, activation='relu', padding='same'))(encoded_rssi)
print(encoded_rssi)
encoded_rssi = TimeDistributed(Flatten())(encoded_rssi)

encoded_rssi=LSTM(128, return_sequences=True)(encoded_rssi)
encoded_rssi=LSTM(128, return_sequences=True)(encoded_rssi)
print("lstm",encoded_rssi)
encoded_rssi=Reshape((T,1,1,128))(encoded_rssi)

print("lstm",encoded_rssi)

N=w
M=h

xy = Input(shape=(T,N,M,1))
print(xy)

encoded = TimeDistributed(Conv2D(32, (3, 3), activation='relu', padding='same'),
        input_shape=(T, N, M, 1))(xy)
encoded = TimeDistributed(MaxPooling2D((2, 2), padding='same'))(encoded)
encoded = TimeDistributed(Conv2D(64, (3, 3), activation='relu', padding='same'))(encoded)
#encoded = TimeDistributed(MaxPooling2D((2, 2), padding='same'))(encoded)
#encoded = TimeDistributed(Conv2D(128, (3, 3), activation='relu', padding='same'))(encoded)
#encoded = TimeDistributed(MaxPooling2D((2, 2), padding='same'))(encoded)
#encoded = TimeDistributed(Conv2D(256, (3, 3), activation='relu', padding='same'))(encoded)
print(encoded)

#LayerNormalization
encoded= ConvLSTM2D(128 , 3,return_sequences=True, padding='same')(encoded)

encoded= ConvLSTM2D(128 , 3,return_sequences=True, padding='same')(encoded)


print(encoded)

#merged=Multiply()([encoded, encoded_rssi])
encoded_rssi2=Reshape((4,128))(encoded_rssi)
print(encoded_rssi2)
print(encoded)
merged=Dot(axes=[4, 2])([encoded, encoded_rssi2])
merged=Softmax()(merged)
# Create a lambda layer to expand dimensions of input2
#expand_dim = Lambda(lambda x: tf.repeat(x, 8, axis=3))(encoded_rssi)  # Repeat along axis 2
#merged=Concatenate(axis=2)([encoded, encoded_rssi])

print(merged)

decoded= ConvLSTM2D(128 , 3, padding='same')(merged)

#decoded = (Conv2D(256, (3, 3), activation='relu', padding='same'))(decoded)
#decoded = (UpSampling2D((2, 2)))(decoded)
#decoded = (Conv2D(128, (3, 3), activation='relu', padding='same'))(decoded)
#decoded = (UpSampling2D((2, 2)))(decoded)
decoded = (Conv2D(64, (3, 3), activation='relu', padding='same'))(decoded)
decoded = (UpSampling2D((2, 2)))(decoded)
decoded = (Conv2D(32, (3, 3), activation='relu', padding='same'))(decoded)
decoded = (Conv2D(1, (3, 3), activation='sigmoid', padding='same'))(decoded)

# Compile model
autoencoder = Model([xy,rssi], decoded)
autoencoder.compile(optimizer='adam', loss='binary_crossentropy', metrics=['mse', 'mae'])
#autoencoder.compile(optimizer=Adam(learning_rate=0.001),
#              loss=CategoricalCrossentropy(),
#              metrics=['accuracy'])

print(encoded)
autoencoder.save("model0.h5")
autoencoder.summary()

2
4
<KerasTensor shape=(None, 4, 2, 1), dtype=float32, sparse=False, name=keras_tensor>


/home/aurora/miniconda3/envs/tf/lib/python3.9/site-packages/keras/src/layers/convolutional/base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)
2025-02-25 14:21:29.623027: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2025-02-25 14:21:29.671571: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2025-02-25 14:21:29.671616: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/

<KerasTensor shape=(None, 4, 2, 64), dtype=float32, sparse=False, name=keras_tensor_2>
lstm <KerasTensor shape=(None, 4, 128), dtype=float32, sparse=False, name=keras_tensor_5>
lstm <KerasTensor shape=(None, 4, 1, 1, 128), dtype=float32, sparse=False, name=keras_tensor_6>
<KerasTensor shape=(None, 4, 8, 8, 1), dtype=float32, sparse=False, name=keras_tensor_7>
<KerasTensor shape=(None, 4, 4, 4, 64), dtype=float32, sparse=False, name=keras_tensor_10>


/home/aurora/miniconda3/envs/tf/lib/python3.9/site-packages/keras/src/layers/core/wrapper.py:27: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


<KerasTensor shape=(None, 4, 4, 4, 128), dtype=float32, sparse=False, name=keras_tensor_12>
<KerasTensor shape=(None, 4, 128), dtype=float32, sparse=False, name=keras_tensor_13>
<KerasTensor shape=(None, 4, 4, 4, 128), dtype=float32, sparse=False, name=keras_tensor_12>
<KerasTensor shape=(None, 4, 4, 4, 4), dtype=float32, sparse=False, name=keras_tensor_15>
<KerasTensor shape=(None, 4, 4, 4, 128), dtype=float32, sparse=False, name=keras_tensor_12>


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 4, 2, 1)   │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ time_distributed    │ (None, 4, 2, 32)  │        128 │ input_layer[0][0] │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_1       │ (None, 4, 8, 8,   │          0 │ -                 │
│ (InputLayer)        │ 1)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ time_distributed_1  │ (None, 4, 2, 64)  │      6,208 │ time_distributed… │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ time_distributed_3  │ (None, 4, 8, 8,   │        320 │ input_layer_1[0]… │
│ (TimeDistributed)   │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ time_distributed_2  │ (None, 4, 128)    │          0 │ time_distributed… │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ time_distributed_4  │ (None, 4, 4, 4,   │          0 │ time_distributed… │
│ (TimeDistributed)   │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm (LSTM)         │ (None, 4, 128)    │    131,584 │ time_distributed… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ time_distributed_5  │ (None, 4, 4, 4,   │     18,496 │ time_distributed… │
│ (TimeDistributed)   │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_1 (LSTM)       │ (None, 4, 128)    │    131,584 │ lstm[0][0]        │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv_lstm2d         │ (None, 4, 4, 4,   │    885,248 │ time_distributed… │
│ (ConvLSTM2D)        │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ reshape (Reshape)   │ (None, 4, 1, 1,   │          0 │ lstm_1[0][0]      │
│                     │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv_lstm2d_1       │ (None, 4, 4, 4,   │  1,180,160 │ conv_lstm2d[0][0] │
│ (ConvLSTM2D)        │ 128)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ reshape_1 (Reshape) │ (None, 4, 128)    │          0 │ reshape[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dot (Dot)           │ (None, 4, 4, 4,   │          0 │ conv_lstm2d_1[0]… │
│                     │ 4)                │            │ reshape_1[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ softmax (Softmax)   │ (None, 4, 4, 4,   │          0 │ dot[0][0]         │
│                     │ 4)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv_lstm2d_2       │ (None, 4, 4, 128) │    608,768 │ softmax[0][0]     │
│ (ConvLSTM2D)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_2 (Conv2D)   │ (None, 4, 4, 64)  │     73,792 │ conv_lstm2d_2[0]

 Total params: 3,055,041 (11.65 MB)

 Trainable params: 3,055,041 (11.65 MB)

 Non-trainable params: 0 (0.00 B)

In [12]:
#MODELO SOLO LSTM

# Rama secuencial
K=len(anchors)

rssi_input = Input(shape=(T, K, 1))
rssi_flattened = TimeDistributed(Flatten())(rssi_input)
rssi_lstm = LSTM(units=128, return_sequences=True)(rssi_flattened)

N=w
M=h

xy_input = Input(shape=(T, N, M, 1))
xy_flattened = TimeDistributed(Flatten())(xy_input)
xy_lstm1 = LSTM(units=256, return_sequences=True)(xy_flattened)  # Mayor capacidad
xy_lstm2 = LSTM(units=128, return_sequences=True)(xy_lstm1)  # Segunda capa LSTM

print(xy_lstm2)

# Aplastando las salidas para que puedan ser concatenadas
rssi_lstm_flattened = Flatten()(rssi_lstm)
xy_lstm_flattened = Flatten()(xy_lstm2)

# Fusión de características

merged = Concatenate()([rssi_lstm_flattened, xy_lstm_flattened])
dense_output = Dense(units=8*8, activation='sigmoid')(merged)
output = Reshape((8, 8, 1))(dense_output)

# Modelo
model = Model(inputs=[xy_input, rssi_input], outputs=output)
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['mse', 'mae'])

model.save("model1.h5")
model.summary()



<KerasTensor shape=(None, 4, 128), dtype=float32, sparse=False, name=keras_tensor_27>


Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_3       │ (None, 4, 8, 8,   │          0 │ -                 │
│ (InputLayer)        │ 1)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_2       │ (None, 4, 2, 1)   │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ time_distributed_7  │ (None, 4, 64)     │          0 │ input_layer_3[0]… │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ time_distributed_6  │ (None, 4, 2)      │          0 │ input_layer_2[0]… │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_3 (LSTM)       │ (None, 4, 256)    │    328,704 │ time_distributed… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_2 (LSTM)       │ (None, 4, 128)    │     67,072 │ time_distributed… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_4 (LSTM)       │ (None, 4, 128)    │    197,120 │ lstm_3[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ flatten_3 (Flatten) │ (None, 512)       │          0 │ lstm_2[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ flatten_4 (Flatten) │ (None, 512)       │          0 │ lstm_4[0][0]      │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate         │ (None, 1024)      │          0 │ flatten_3[0][0],  │
│ (Concatenate)       │                   │            │ flatten_4[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 64)        │     65,600 │ concatenate[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ reshape_2 (Reshape) │ (None, 8, 8, 1)   │          0 │ dense[0][0]       │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 658,496 (2.51 MB)

 Trainable params: 658,496 (2.51 MB)

 Non-trainable params: 0 (0.00 B)

In [13]:
#MODELO LIGERO: LSTM+CONV+LSTM

# Rama secuencial
K=len(anchors)
print(K)

rssi = Input(shape=(T,K,1))
print(rssi)
lstm1=TimeDistributed(Flatten())(rssi)

lstm_out = LSTM(units=128)(lstm1)
print("LSTM",lstm_out)

N=w
M=h

print(w,h)

xy = Input(shape=(T,N,M,1))
print(xy)

conv1 = Conv2D(filters=32, kernel_size=(3, 3), padding='same', activation='relu')(xy)
conv2 = Conv2D(filters=64, kernel_size=(3, 3), padding='same', activation='relu')(conv1)
conv_out = TimeDistributed(Flatten())(conv2)
print("CONV",conv_out)

lstm2= LSTM(units=1024,return_sequences=True)(conv_out)
lstm2_out=LSTM(units=128,return_sequences=True)(lstm2)
lstm2_out=Flatten()(lstm2_out)
print(lstm2_out)

# Fusión de características

merged = Concatenate()([lstm_out, lstm2_out])
dense1 = Dense(128, activation='relu')(merged)
reshape = Reshape((2, 2, 32))(dense1) 


# Deconvolución para generar imagen
conv2dtranspose1 = Conv2DTranspose(filters=64, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='relu')(reshape)
conv2dtranspose2 = Conv2DTranspose(filters=1, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='sigmoid')(conv2dtranspose1)

# Modelo
model = Model(inputs=[xy, rssi], outputs=conv2dtranspose2)
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['mse', 'mae']) 

model.save("model2.h5")
model.summary()

2
<KerasTensor shape=(None, 4, 2, 1), dtype=float32, sparse=False, name=keras_tensor_33>
LSTM <KerasTensor shape=(None, 128), dtype=float32, sparse=False, name=keras_tensor_35>
8 8
<KerasTensor shape=(None, 4, 8, 8, 1), dtype=float32, sparse=False, name=keras_tensor_36>


ValueError: Kernel shape must have the same length as input, but received kernel of shape (3, 3, 1, 32) and input of shape (None, 4, 8, 8, 1).

In [ ]:
#MODELO LIGERO2: LSTM+CONV+LSTM con DROPOUT Y BATCHNORMALIZATION

# Rama secuencial
K=len(anchors)
print(K)

rssi = Input(shape=(T,K,1))
print(rssi)
lstm1=TimeDistributed(Flatten())(rssi)

lstm_out = LSTM(units=128,dropout=0.2)(lstm1)
print("LSTM",lstm_out)

N=w
M=h

print(w,h)

xy = Input(shape=(T,N,M,1))
print(xy)

conv1 = Conv2D(filters=32, kernel_size=(3, 3), padding='same', activation='relu')(xy)
conv1 = BatchNormalization()(conv1)  # Añadido BatchNormalization
conv2 = Conv2D(filters=64, kernel_size=(3, 3), padding='same', activation='relu')(conv1)
conv2 = BatchNormalization()(conv2)  # Añadido BatchNormalization
conv_out = TimeDistributed(Flatten())(conv2)
print("CONV",conv_out)

lstm2= LSTM(units=1024,return_sequences=True,dropout=0.2)(conv_out)
lstm2_out=LSTM(units=128,return_sequences=True,dropout=0.2)(lstm2)
lstm2_out=Flatten()(lstm2_out)
print(lstm2_out)

# Fusión de características

merged = Concatenate()([lstm_out, lstm2_out])
dense1 = Dense(128, activation='relu')(merged)
reshape = Reshape((2, 2, 32))(dense1) 


# Deconvolución para generar imagen
conv2dtranspose1 = Conv2DTranspose(filters=64, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='relu')(reshape)
conv2dtranspose2 = Conv2DTranspose(filters=1, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='sigmoid')(conv2dtranspose1)

# Modelo
modelA2 = Model(inputs=[xy, rssi], outputs=conv2dtranspose2)
modelA2.compile(optimizer='adam', loss='binary_crossentropy', metrics=['mse', 'mae']) 

modelA2.save("model3.h5")
modelA2.summary()

In [ ]:
#MODELO CON ATTENTIONAL DE 128

from keras.layers import Input, LSTM, Dense, Concatenate, Reshape, Conv2D, Conv2DTranspose, TimeDistributed, Flatten, BatchNormalization, Dropout, Layer
import keras.backend as KE
from tensorflow.keras.utils import register_keras_serializable

@register_keras_serializable()
class Attention(layers.Layer):
    def __init__(self, units=128, **kwargs):
        super(Attention, self).__init__(**kwargs)
        self.W1 = Dense(units)
        self.W2 = Dense(units)
        self.V = Dense(1)

    def call(self, features, hidden):
        # hidden shape == (batch_size, hidden size)
        hidden_with_time_axis = KE.expand_dims(hidden, 1)
        
        # score shape == (batch_size, max_length, hidden size)
        score = KE.tanh(self.W1(features) + self.W2(hidden_with_time_axis))
        
        # attention_weights shape == (batch_size, max_length, 1)
        attention_weights = KE.softmax(self.V(score), axis=1)
        
        # context_vector shape after sum == (batch_size, hidden size)
        context_vector = attention_weights * features
        context_vector = KE.sum(context_vector, axis=1)

        return context_vector, attention_weights

    def compute_output_shape(self, input_shape):
        return input_shape[0], input_shape[-1]

    def get_config(self):
        base_config = super(Attention, self).get_config()
        return base_config
    
    
# Rama secuencial
K=len(anchors)
print(K)

rssi = Input(shape=(T,K,1))
print(rssi)
lstm1=TimeDistributed(Flatten())(rssi)

lstm_out = LSTM(units=128,dropout=0.2)(lstm1)
print("LSTM",lstm_out)

N=w
M=h

print(w,h)

xy = Input(shape=(T,N,M,1))
print(xy)

conv1 = Conv2D(filters=32, kernel_size=(3, 3), padding='same', activation='relu')(xy)
conv1 = BatchNormalization()(conv1)  # Añadido BatchNormalization
conv2 = Conv2D(filters=64, kernel_size=(3, 3), padding='same', activation='relu')(conv1)
conv2 = BatchNormalization()(conv2)  # Añadido BatchNormalization
conv_out = TimeDistributed(Flatten())(conv2)
print("CONV",conv_out)

lstm2= LSTM(units=1024,return_sequences=True,dropout=0.2)(conv_out)
lstm2= LSTM(units=128,return_sequences=True,dropout=0.2)(lstm2)
lstm2_out=LSTM(units=32,return_sequences=True,dropout=0.2)(lstm2)
lstm2_out=Flatten()(lstm2_out)
print("LSTM2",lstm2_out)

# Aplicando atención a la salida de la primera LSTM
attention_layer = Attention(128)
context_vector1, attention_weights1 = attention_layer(lstm_out, lstm_out)

# Aplicando atención a la salida de la segunda LSTM
context_vector2, attention_weights2 = attention_layer(lstm2_out, lstm2_out)

# Fusión de características con vectores de contexto de capas de atención
merged = Concatenate()([context_vector1, context_vector2])
dense1 = Dense(128, activation='relu')(merged)
reshape = Reshape((2, 2, 32))(dense1)

# Deconvolución para generar imagen
conv2dtranspose1 = Conv2DTranspose(filters=64, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='relu')(reshape)
conv2dtranspose2 = Conv2DTranspose(filters=1, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='sigmoid')(conv2dtranspose1)

# Modelo
modelA2 = Model(inputs=[xy, rssi], outputs=conv2dtranspose2)
modelA2.compile(optimizer='adam', loss='binary_crossentropy', metrics=['mse', 'mae']) 
modelA2.save("model4.h5")
modelA2.summary()


In [ ]:
from keras.layers import Multiply

def apply_attention_2d(inputs):
    # Genera mapas de atención usando una convolución
    attention_map = Conv2D(filters=1, kernel_size=(3, 3), padding='same', activation='sigmoid')(inputs)
    
    # Aplica el mapa de atención a los inputs (element-wise multiplication)
    attended_inputs = Multiply()([inputs, attention_map])
    
    return attended_inputs


# Rama secuencial
K=len(anchors)
print(K)

rssi = Input(shape=(T,K,1))
print(rssi)
lstm1=TimeDistributed(Flatten())(rssi)

lstm_out = LSTM(units=128,dropout=0.2)(lstm1)
print("LSTM",lstm_out)

N=w
M=h

print(w,h)

xy = Input(shape=(T,N,M,1))
print(xy)

conv1 = Conv2D(filters=32, kernel_size=(3, 3), padding='same', activation='relu')(xy)
# Aplicando atención 2D después de las convoluciones en tu modelo
conv1_attended = apply_attention_2d(conv1)
conv2 = Conv2D(filters=64, kernel_size=(3, 3), padding='same', activation='relu')(conv1_attended)
conv2_attended = apply_attention_2d(conv2)
conv2 = BatchNormalization()(conv2_attended) 
conv_out = TimeDistributed(Flatten())(conv2)
print("CONV",conv_out)

lstm2= LSTM(units=1024,return_sequences=True,dropout=0.2)(conv_out)
lstm2_out=LSTM(units=128,return_sequences=True,dropout=0.2)(lstm2)
lstm2_out=Flatten()(lstm2_out)
print(lstm2_out)

# Fusión de características

merged = Concatenate()([lstm_out, lstm2_out])
dense1 = Dense(128, activation='relu')(merged)
reshape = Reshape((2, 2, 32))(dense1) 


# Deconvolución para generar imagen
conv2dtranspose1 = Conv2DTranspose(filters=64, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='relu')(reshape)
conv2dtranspose2 = Conv2DTranspose(filters=1, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='sigmoid')(conv2dtranspose1)

# Modelo
modelA2 = Model(inputs=[xy, rssi], outputs=conv2dtranspose2)
modelA2.compile(optimizer='adam', loss='binary_crossentropy', metrics=['mse', 'mae']) 

modelA2.save("model5.h5")
modelA2.summary()

In [ ]:
#MODELO CON ATTENTIONAL QUE TIENE EN CUENTA PESOS  
    
# Rama secuencial
K=len(anchors)
print(K)

rssi = Input(shape=(T,K,1))
print(rssi)
lstm1=TimeDistributed(Flatten())(rssi)

lstm_out = LSTM(units=128,dropout=0.2)(lstm1)
print("LSTM",lstm_out)

N=w
M=h

print(w,h)

xy = Input(shape=(T,N,M,1))
print(xy)

conv1 = Conv2D(filters=32, kernel_size=(3, 3), padding='same', activation='relu')(xy)
conv1 = BatchNormalization()(conv1)  # Añadido BatchNormalization
conv2 = Conv2D(filters=64, kernel_size=(3, 3), padding='same', activation='relu')(conv1)
conv2 = BatchNormalization()(conv2)  # Añadido BatchNormalization
conv_out = TimeDistributed(Flatten())(conv2)
print("CONV",conv_out)

lstm2= LSTM(units=1024,return_sequences=True,dropout=0.2)(conv_out)
lstm2= LSTM(units=128,return_sequences=True,dropout=0.2)(lstm2)
lstm2_out=LSTM(units=32,return_sequences=True,dropout=0.2)(lstm2)
lstm2_out=Flatten()(lstm2_out)
print("LSTM2",lstm2_out)


# Primero, aplicamos la capa de atención a la salida de lstm_out_128
attention_layer_128 = Attention(128)
context_vector_128, attention_weights_128 = attention_layer_128(lstm_out, lstm_out)


# Aplicando atención a la salida de la segunda LSTM
attention_layer_512 = Attention(512)
context_vector_512, attention_weights_512 = attention_layer_512(lstm2_out, lstm2_out)

# Fusión de características con vectores de contexto de capas de atención
merged = Concatenate()([context_vector_128, context_vector_512])
dense1 = Dense(128, activation='relu')(merged)
reshape = Reshape((2, 2, 32))(dense1)

# Deconvolución para generar imagen
conv2dtranspose1 = Conv2DTranspose(filters=64, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='relu')(reshape)
conv2dtranspose2 = Conv2DTranspose(filters=1, kernel_size=(3, 3), strides=(2, 2), padding='same', activation='sigmoid')(conv2dtranspose1)

# Modelo
modelA2 = Model(inputs=[xy, rssi], outputs=conv2dtranspose2)
modelA2.compile(optimizer='adam', loss='binary_crossentropy', metrics=['mse', 'mae']) 

modelA2.save("model6.h5")
modelA2.summary()


In [ ]:
def plotting(XYT_test,YT_test,YT_prediction):
    K=5
    off=3

    # Create a figure with two subplots (one row, two columns)
    fig, axes = plt.subplots(K, 3, figsize=(20, 20))

    for k in range(0,K):
        mpAll=XYT_test[k+off][T-1].reshape(N,M)

        axes[k,0].imshow(mpAll, cmap='viridis', interpolation='nearest')
        axes[k,0].set_title('All players (last frame)')
        axes[k,0].axis('off')

        label=rssiT_test[k+off][T-1]
        mpOne=YT_test[k+off].reshape(N,M)

        axes[k,1].imshow(mpOne, cmap='viridis', interpolation='nearest')
        axes[k,1].set_title('True (last frame) of player')
        axes[k,1].axis('off')


        mpPrediction=YT_prediction[k+off].reshape(N,M)

        axes[k,2].imshow(mpPrediction, cmap='viridis', interpolation='nearest')
        axes[k,2].set_title('Prediction of player ')
        axes[k,2].axis('off')


    # Adjust spacing between subplots
    plt.tight_layout()

    # Show the plots
    plt.show()

In [ ]:
def plottingRandom(XYT_test,YT_test,YT_prediction):
    K=5
    ks=np.random.randint(0, len(test_indices), K)

    # Create a figure with two subplots (one row, two columns)
    fig, axes = plt.subplots(K, 3, figsize=(20, 20))

    for k in range(0,K):
        mpAll=XYT_test[ks[k]][T-1].reshape(N,M)

        axes[k,0].imshow(mpAll, cmap='viridis', interpolation='nearest')
        axes[k,0].set_title('All players (last frame)')
        axes[k,0].axis('off')

        label=rssiT_test[ks[k]][T-1]
        mpOne=YT_test[ks[k]].reshape(N,M)

        axes[k,1].imshow(mpOne, cmap='viridis', interpolation='nearest')
        axes[k,1].set_title('True (last frame) of player')
        axes[k,1].axis('off')


        mpPrediction=YT_prediction[ks[k]].reshape(N,M)

        axes[k,2].imshow(mpPrediction, cmap='viridis', interpolation='nearest')
        axes[k,2].set_title('Prediction of player ')
        axes[k,2].axis('off')


    # Adjust spacing between subplots
    plt.tight_layout()

    # Show the plots
    plt.show()

In [ ]:
import numpy as np
import time
from sklearn.metrics import mean_squared_error, mean_absolute_error

np.random.seed(42)

# Lista de identificadores de modelo
model_ids = ["model0","model1","model2","model4"] 

# Estructuras para almacenar resultados y tiempos de ejecución
mse_results = {model_id: [] for model_id in model_ids}
mae_results = {model_id: [] for model_id in model_ids}
training_times = {model_id: [] for model_id in model_ids}
total_execution_time = {model_id: 0 for model_id in model_ids}

print(np.unique(S))

for ixs, sc in enumerate(np.unique(S)):
    # Índices para entrenamiento y prueba
    train_indices = np.where(S != sc)[0]
    test_indices = np.where(S == sc)[0]
    np.random.shuffle(train_indices)

    XYT_train = XYT[train_indices]
    rssiT_train = rssiT[train_indices]
    YT_train = YT[train_indices]

    XYT_test = XYT[test_indices]
    rssiT_test = rssiT[test_indices]
    YT_test = YT[test_indices]
    
    for model_id in model_ids:
        print(f"MODELO {model_id} - ESCENA {sc}")
        
        model = load_model(f"{model_id}.h5")

        start_time = time.time()

        history = model.fit([XYT_train, rssiT_train], YT_train,
                                  batch_size=16,
                                  validation_data=([XYT_test, rssiT_test], YT_test),
                                  epochs=50)
        end_time = time.time()
        training_time = end_time - start_time
        
        YT_prediction = model.predict([XYT_test, rssiT_test])

        plottingRandom(XYT_test, YT_test, YT_prediction)

        mse = mean_squared_error(YT_test.flatten(), YT_prediction.flatten())
        mae = mean_absolute_error(YT_test.flatten(), YT_prediction.flatten())

        mse_results[model_id].append(mse)
        mae_results[model_id].append(mae)
        training_times[model_id].append(training_time)
        total_execution_time[model_id] += training_time

# Calculando promedios y mostrando resultados

print("Resultados por escena:")
for i, sc in enumerate(np.unique(S)):
    print(f"Escena {sc}:")
    for model_id in model_ids:
        print(f"Modelo {model_id} - MSE: {mse_results[model_id][i]:.4f}, MAE: {mae_results[model_id][i]:.4f}, Tiempo: {training_times[model_id][i]:.2f}s")
    print("")
    
print("RESUMEN RESULTADOS:")
for model_id in model_ids:
    average_mse = np.mean(mse_results[model_id])
    average_mae = np.mean(mae_results[model_id])
    print(f"Modelo {model_id}:")
    print(f"Tiempo de ejecución total: {total_execution_time[model_id]:.2f} segundos")
    print(f"MSE promedio: {average_mse:.4f}")
    print(f"MAE promedio: {average_mae:.4f}\n")


In [ ]:
for it,tt in enumerate(ts):
    print(it,tt)